In [33]:
import os
import json
import numpy as np
import pandas as pd
from pandas.io.json import json_normalize

import matplotlib.pyplot as plt
import seaborn as sns
color = sns.color_palette()
def load_df(json_path='./project/dblp-ref-3.json', nrows=None):
    train = pd.read_json(json_path, lines=True)
    train.reset_index(level=0, inplace=True)
    train.head()
    return train

In [34]:
train_df = load_df()
train_df.head()
# len(train_df)
# dict_paper_refs = {}

79007

In [5]:
train_df.describe()
venues= train_df.venue.unique()
venues[:100]

array(['high performance computing and communications',
       'international conference on conceptual structures',
       'international conference on control, automation, robotics and vision',
       'Communications of The ACM', 'Journal of Computational Chemistry',
       '', 'Frontiers in Digital Humanities',
       'international symposium on information theory and its applications',
       'international conference on machine learning and applications',
       'international symposium on mixed and augmented reality',
       'tools and algorithms for construction and analysis of systems',
       'panhellenic conference on informatics',
       'arXiv: Artificial Intelligence',
       'global communications conference', 'arXiv: Information Theory',
       'Lecture Notes in Computer Science', 'arXiv: Robotics',
       'Mobile Information Systems',
       'Informatica (lithuanian Academy of Sciences)', 'Neurocomputing',
       'European Journal of Operational Research',
       'Intell

# Calculating h-index for authors

In [86]:
def get_h_index(citations):
#     Creating a dict of paper id and its references
    citations.sort()
    n = len(citations)
    for i in range(n):
        if citations[i] >= (n-i):
            return n-i
    return 0
        
    
    
    
#     create author-papers map
#     get citation count of a paper from Graph
#     create citation array for each author
#     calculate h-index for each author, put it in a map
def get_author_paper_map(df, G):
    author_paper_map = dict()
    author_papercitations_map = dict()
    authors_all = df.authors.tolist()
    for i in range(0, len(authors_all)):
        
        authors = authors_all[i]
        for j in range(0, len(authors)):
            author = authors[j]
#             print (author)
            if author not in author_paper_map:
                author_paper_map[author] =  set()
                author_paper_map[author].add(df.id[i])
                author_papercitations_map[author] =  []
                author_papercitations_map[author].append(len(list(G.predecessors(df.id[i]))))
            else:
                author_paper_map[author].add(df.id[i])
                author_papercitations_map[author].append(len(list(G.predecessors(df.id[i]))))
                
#     print (author_paper_map)
    return author_paper_map ,author_papercitations_map


In [87]:
import networkx as nx
def get_paper_graph(df):
    G = nx.DiGraph()
#     G.add_node(1)
    G.add_nodes_from(df.id[0:10000])
    for i in range (0, 10000):#len((df.id))
#         print (len(df.references[0]))
        paper_id = df.id[i]
        if(df.references[i] is "NA"):
            continue  
        for j in range(0, len(df.references[i])):
            refs= df.references[i]
            G.add_edge(paper_id, refs[j])
    return G
    

train_df['references'] = train_df['references'].fillna("NA")
G=get_paper_graph(train_df)
print("Edges Count:"+str(len(list(G.edges))))
# print (G.predecessors('001eef4f-1d00-4ae6-8b4f-7e66344bbc6e'))
# preds= list(G.predecessors('001eef4f-1d00-4ae6-8b4f-7e66344bbc6e'))
# print(len(list(preds)))
author_paper_map, author_papercitations_map = get_author_paper_map(train_df[0:10000], G)

Edges Count:69062


In [88]:
print (len(author_papercitations_map))
def get_author_h_index(author_papercitations_map):
    author_h_index_map = {}
    for author, citations in author_papercitations_map.items():
        h_index= get_h_index(citations)
        author_h_index_map[author] =  h_index
    return author_h_index_map

author_h_index_map = get_author_h_index(author_papercitations_map)
print("Authors with h-index>0")
for author, h_index in author_h_index_map.items():
       if h_index>0:
            print (author + ":"+ str(h_index))

28551
Authors with h-index>0
Monika Sharma:1
Ramya Hebbalaguppe:1
Ehtesham Hassan:1
Lovekesh Vig:1
Andrew Warren:1
Jekan Thangavelautham:1
Jinwei Liu:2
Haiying Shen:2
J. Nathan Kutz:1
Steven L. Brunton:1
Bingni W. Brunton:1
Joshua L. Proctor:1
Yong Huang:1
George K. Karagiannidis:1
Diego Furtado Silva:1
Eamonn J. Keogh:1
Yan Zhu:1
Evangelos E. Papalexakis:1
Christos Faloutsos:1
David G. C. Hildebrand:1
Marko Niemimaa:1
Hoang Dau:1
Shouhuai Xu:1
Kai Zhao:1
Yunhe Pan:1
Huy T. Vo:1
Tom Vierjahn:1
Torsten Kuhlen:1
Matthias S. Müller:1
Bernd Hentschel:1
Weixiang Shao:1
Bokai Cao:1
Philip S. Yu:1
Jeffrey S. Saltz:1
Ivan Shamshurin:1
Jonathan Stokes:1
Steven Weber:1
Yonghong Tian:1
Xilin Chen:1
Hongkai Xiong:1
Hongliang Li:1
Li-Rong Dai:1
Jing Chen:1
Junliang Xing:1
Xihong Wu:1
Weiming Hu:1
Yu Hu:1
Tiejun Huang:1
Wen Gao:1
Seung-Hwan Lim:1
Dong Wang:1
Tao Zhang:1
Gautam Shroff:1
Mimansa Jaiswal:1
Sairam Tabibu:1
Rajiv Bajpai:1
Hamdi Amroun:1
Nizar Ouarti:1
Mehdi Ammi:1
Berkay Aydin:1
Rafal A.

In [80]:
import requests
import re
def get_field_of_study(df_titles=None):
    print(len(df_titles))
    df_titles_copy = df_titles.copy()
#     titles = ['temporal languages for simulation and analysis of the dynamics within an organisation','on leveraging executable language engineering for domain specific transformation languages'] 
#     payload = {'expr': 'Or(Ti==\'on leveraging executable language engineering for domain specific transformation languages\', Ti=\'temporal languages for simulation and analysis of the dynamics within an organisation\')', 'attributes': 'Ti,AA.AuN,AA.AuId,F.FN'}
#     headers = {'Ocp-Apim-Subscription-Key': '78488b64dc7541f1a80ba499b9c5f8ff'}
#     req = requests.get('https://api.labs.cognitive.microsoft.com/academic/v1.0/evaluate', params=payload, headers=headers)
#     response = req.json()
    field1=[]
    field2=[]
    field3=[]
    index = 0
    while index<len(df_titles):#len(df_titles)
        titles = []
        if index +10 < len(df_titles):
            titles=df_titles[index:index+10]
#             titles = titles.reset_index()
            print(len(titles))
        else:
            titles=df_titles[index:]
#         print(titles[0])
#         print(str(titles.iloc[1]))
    #     payload = {'expr': 'Or(Ti==\'on leveraging executable language engineering for domain specific transformation languages\', Ti=\'temporal languages for simulation and analysis of the dynamics within an organisation\')', 'attributes': 'Ti,AA.AuN,AA.AuId,F.FN'}
        titles_str = ''

        for j in range(0, len(titles)):#len(titles)
            titles.iloc[j] = titles.iloc[j].replace("-"," ")
            titles.iloc[j] = titles.iloc[j].replace(":"," ")
            titles.iloc[j] = titles.iloc[j].replace("/"," ")
            titles.iloc[j] = titles.iloc[j].replace(".","")
            titles.iloc[j] = str(titles.iloc[j]).lower()
            titles.iloc[j] = re.sub('[^a-z0-9 \.]', '', titles.iloc[j])
            titles.iloc[j] = re.sub(' +',' ',titles.iloc[j])
            if j != len(titles)-1:
                titles_str=titles_str+'Ti==\''+str(titles.iloc[j])+'\','
            else:
                titles_str=titles_str+'Ti==\''+str(titles.iloc[j])+'\''
        payload = {'expr': 'Or('+titles_str+')', 'attributes': 'Ti,AA.AuN,AA.AuId,F.FN'}
#         print (payload)
        
        keys = ['78488b64dc7541f1a80ba499b9c5f8ff', '7434d131465f4c34a9ca2ac588849179','688fe6d13aab4295888a0616a1be4f32','74bbebc90d204016a1e9e5d9592d5812']
        k = index%len(keys)
        headers = {'Ocp-Apim-Subscription-Key': keys[k]}
        import time
        if index%5==0:
            time.sleep(.300)
            time.sleep(.300)
            time.sleep(.100)
        req = requests.get('https://api.labs.cognitive.microsoft.com/academic/v1.0/evaluate', params=payload, headers=headers)
        if req.status_code != 200:
            print(index) 
            print ("FAILED WITH STATUS"+ str(req.status_code))
        response = req.json()
        
        for j in range(0, len(titles)):
            print('TITLE: ',titles.iloc[j])
            if response is not None:
                if response.get('entities') is not None:

                    for i in range(0,len(response.get('entities'))):
                        if response.get('entities')[i].get('Ti')!=titles.iloc[j]:
                            continue
                        titles.iloc[j]='visited'
                        if response.get('entities')[i].get('F') is not None:
                            fields = response.get('entities')[i].get('F')
#                             print(fields)
#                             print(len(fields))
                            fields_size = len(fields)
                    #         for i in range(len(fields-1, len(fields)-4,-1 ):
                            if fields_size > 2:
                                field1.append(fields[fields_size-1].get('FN'))
                                field2.append(fields[fields_size-2].get('FN'))
                                field3.append(fields[fields_size-3].get('FN'))

                            elif fields_size == 2:
                                field1.append(fields[fields_size-1].get('FN'))
                                field2.append(fields[fields_size-2].get('FN'))
                                field3.append('NA')
                            elif fields_size == 1:
                                field1.append(fields[fields_size-1].get('FN'))
                                field2.append('NA')
                                field3.append('NA')
                            else:
                                field1.append('NA')
                                field2.append('NA')
                                field3.append('NA')

            if len(field1)-1<index:
                field1.append('NA')
            if len(field2)-1<index:
                field2.append('NA')
            if len(field3)-1<index:
                field3.append('NA')
#             print(field3[index]+' '+field2[index]+' '+field1[index])
            index=index+1
#         print(len(field1))
#         print(len(field2))
#         print(len(field3))
        if (index%100==0 and index>0):
            print('write to file')
            title_field = pd.DataFrame(
            {'title': df_titles_copy[index-100:index], 'field1': field1[index-100:index], 'field2': field2[index-100:index], 'field3': field3[index-100:index]},
            columns = ['title', 'field1', 'field2','field3'])
            title_field.to_csv('fields_dblp-ref-3.csv', mode='a',index = False, header=False)
            print('Completed: 'index)
    if (index%100!=0 and index>0):
        print('last write to file')
        title_field = pd.DataFrame(
        {'title': df_titles_copy[index-(index%100):index], 'field1': field1[index-(index%100):index], 'field2': field2[index-(index%100):index], 'field3': field3[index-(index%100):index]},
        columns = ['title', 'field1', 'field2','field3'])
        title_field.to_csv('fields_dblp-ref-3.csv', mode='a',index = False, header=False)

In [81]:
df_titles = train_df.title.copy()
get_field_of_study(df_titles)

79007
10
TITLE:  a heterogeneous system for real time detection with adaboost
TITLE:  a novel conformal jigsaw ebg structure design
TITLE:  a source seeking strategy for an autonomous underwater vehicle via on line field estimation
TITLE:  social and ethical behavior in the internet of things
TITLE:  prediction of consensus binding mode geometries for related chemical series of positive allosteric modulators of adenosine and muscarinic acetylcholine receptors
TITLE:  data driven relevance judgments for ranking evaluation
TITLE:  studying linguistic changes over 200 years of newspapers through resilient words analysis
TITLE:  small secret exponent attacks on rsa with unbalanced prime factors
TITLE:  automatic container code recognition via spatial transformer networks and connected component region proposals
TITLE:  effective solution for a medical tourism aggregative system using the data mining approach
10
TITLE:  modeling physical structure as additional constraints for stereoscopic 

TITLE:  a robust and secure rfid based pedigree system short paper
TITLE:  modellbasierte und modellgetriebene softwaremodernisierung bericht ber den workshop im rahmen der konferenz modellierung 2016
TITLE:  disentangling resting state bold variability and pcc functional connectivity in 22q112 deletion syndrome
TITLE:  design control and visual navigation of the delftacopter
TITLE:  engineering future interoperable and open iot systems
TITLE:  an interpretation of isabelle hol in hol light
TITLE:  iot in action design and implementation of a building evacuation service
TITLE:  discovering conversational dependencies between messages in dialogs
TITLE:  extending soft sets towards the optimality of decision based on multiple decisions over the same data
TITLE:  dynamic mode decomposition data driven modeling of complex systems
10
TITLE:  left ventricle basal region constrained parametric mapping to unitary domain
TITLE:  qos assurance with light virtualization a survey
TITLE:  pedestria

TITLE:  framework for a hospitality big data warehouse the implementation of an efficient hospitality business intelligence system
TITLE:  social media and analytics for competitive performance a conceptual research framework
TITLE:  encapsulating models and approximate inference programs in probabilistic modules
TITLE:  on the interest of data mining for an integrity assessment of ais messages
TITLE:  exploiting convolutional neural network for risk prediction with medical feature embedding
TITLE:  optimized two level parallelization for gpu accelerators using the polyhedral model
TITLE:  synchronization free automatic parallelization for arbitrarily nested affine loops
TITLE:  decentralized random walk based data collection in networks
TITLE:  grid service selection with ppdl
TITLE:  bayesian processing of vestibular information
10
TITLE:  codes for channels with segmented edits
TITLE:  measurement experiments and analysis for modeling of mckibben pneumatic actuator
TITLE:  xml schem

TITLE:  a joint design of timing tracking and channel estimation for idma receivers
TITLE:  wie lehrt man requirements engineering ein erfahrungsbericht
TITLE:  a green program lifecycle supporting energy efficient applications
TITLE:  dynamic symbolic execution for polymorphism
TITLE:  normalizing digital news stories for preservation
TITLE:  segmentation and registration coupling from short axis cine mri application to infarct diagnosis
TITLE:  predicting the reliability of resources in computational grid
TITLE:  examining the antecedents and outcomes of erp implementation success an explanatory study
TITLE:  robust visual tracking based on scale invariance and deep learning
TITLE:  predicting soccer highlights from spatio temporal match event streams
10
TITLE:  exploiting traces in program analysis
TITLE:  study on a two link horizontal bar gymnastics robot with passive joint motion control using feedforward control based on inverse dynamics
TITLE:  kalman based time varying sparse 

TITLE:  is game based learning better in flow experience and various types of cognitive load than non game based learning perspective from multimedia and media richness
TITLE:  pure parsimony xor haplotyping
TITLE:  tightly integrated probabilistic description logic programs for the semantic web
TITLE:  a new finite volume approach for transport models and related applications with balancing source terms
TITLE:  stability analysis and control in the process of floating target capture with hardware in the loop system
TITLE:  lightweight hardware architectures for fault diagnosis schemes of efficiently maskable cryptographic substitution boxes
TITLE:  less is more minimizing code reorganization using xtree
TITLE:  object class segmentation of rgb d video using recurrent convolutional neural networks
TITLE:  related event discovery
TITLE:  an inductive 2 d position detection ic with 998 accuracy for automotive emr gear control system
10
TITLE:  lower bounds for clear transmissions in radi

...

TITLE:  a hypothetical reasoning system for mobile health and wellness applications
TITLE:  task condition and pupillometry
TITLE:  optimal consumption and investment with fixed and proportional transaction costs
TITLE:  sigact tutorial session
TITLE:  voice and speech assessment from telephone recordings using prosodic analysis based on u law companded features
TITLE:  dashboard visualizations supporting real time throughput decision making
TITLE:  wealth and strategic financial consumption pricing
TITLE:  legalbot a deep learning based conversational agent in the legal domain
TITLE:  stylometric authorship attribution of collaborative documents
TITLE:  codifying architecture knowledge to support online evolution of software product lines
10
TITLE:  experience of using message spooling processors in a non interactive network
TITLE:  height field construction using cross contours
TITLE:  graphbased recommendation integrating rating history and domain knowledge application to onsite gui

TITLE:  polimake a policy making engine for secure embedded software execution on chip multiprocessors
TITLE:  a pathway from web to telephone to save patients in emergency transfer applied to a long term care system for high risk pregnancy in mie prefecture
TITLE:  catalyst piloting capabilities for more transparent text analytics
TITLE:  tunneling through alternative facts the qwand problem space machine
TITLE:  synthesis of pdzno core shell nanoparticles with different size and their gas sensing properties
TITLE:  on sum rate maximization approach to network beamforming and power allocation for asynchronous single carrier two way relay networks
TITLE:  wearable sensor based activity recognition for housekeeping task
TITLE:  introducing causality in business rule based decisions
TITLE:  enhancing knowledge and skill chains in manufacturing and engineering
TITLE:  robust copy move forgery revealing in digital images using polar coordinate system
10
TITLE:  personalised fading for stre

TITLE:  scalable and distributed key value store based data management using rdma memcached
TITLE:  a novel methodology for stock investment using high utility episode mining and genetic algorithm
TITLE:  comparison of drug drug interaction alert acceptance rates
TITLE:  methods to measure and improve the quality of large scale health data an application in public health surveillance
TITLE:  state of the geotags motivations and recent changes
TITLE:  asthma ascertainment nlp system portability across institutions
TITLE:  on approximate welfare and revenue maximizing equilibria for size interchangeable bidders
TITLE:  together yet apart the research prototype architecture dilemma
TITLE:  on a property of non liouville numbers
TITLE:  field division routing
10
TITLE:  understanding patient satisfaction with received healthcare services a natural language processing approach
TITLE:  the development and evaluations of the appointment system for clinics through i mode and www
TITLE:  a prim

TITLE:  dotproject open source software for project management education
TITLE:  understanding the knowledge gap experienced by us safety net patients in teleretinal screening
TITLE:  sozial auch ohne netz soziale medien bei infrastrukturproblemen
TITLE:  resources for analyzing drug prescription datasets
TITLE:  an improved ieee 802154 superframe structure with minimum delay and maximum cfp link utilization
TITLE:  lattice based revocable identity based encryption with bounded decryption key exposure resistance
TITLE:  instability of fifo in the permanent sessions model at arbitrarily small network loads
TITLE:  debugging of constraint programs the discipl methodology and tools introduction
TITLE:  evolving distributed control for an object clustering task
TITLE:  a complex system characterization of modern telecommunication services
10
TITLE:  word level identification of romanized tunisian dialect
TITLE:  hierarchical submission in a grid environment
TITLE:  from iot big data to iot

TITLE:  sparse discriminative feature selection for multi class alzheimers disease classification
TITLE:  visualization of topics from twitter and focus groups as the foundation for insights about dementia caregiving
TITLE:  service oriented domain and business process modelling
TITLE:  facies classification from well logs using an inception convolutional network
TITLE:  a new dynamic model for anticipatory adaptive control of airline seat reservation via order statistics of cumulative customer demand
TITLE:  characterization of temporal semantic shifts of peer to peer communication in a health related online community implications for data driven health promotion
TITLE:  tracking the remodeling of snomed cts bacterial infectious diseases
TITLE:  on unifying deep generative models
TITLE:  cognition enabled task interpretation for human robot teams in a simulation based search and rescue mission
TITLE:  a map ins wi fi integrated system for indoor location based service applications
10


In [85]:
# len(df_titles)
# print (train_df.title[0:1007].tail(10))
data = pd.read_csv("fields_dblp-ref-3.csv", names=['Title', 'F1', "F2",'F3']) 
print(len(data))
# data.tail(10)
# data.Title
# set(data.Title).difference(set(train_df.title[0:1007]))
# print (len(set(data.Title)))
# print (len(set(train_df.title[0:1007])))

79007
